In [20]:
import torchaudio
import torch

In [23]:
SAMPLE_RATE = 22050

In [13]:
example_waveform, _ = torchaudio.load("wavfiles/11713-0.wav")

In [24]:
from vscode_audio import Audio
Audio(example_waveform.numpy(), sr=SAMPLE_RATE)

In [25]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
bundle = torchaudio.pipelines.WAV2VEC2_BASE
model = bundle.get_model().to(device)

In [26]:
with torch.inference_mode():
  features, _ = model.extract_features(example_waveform.to(device))

In [50]:
from tensorboardX import SummaryWriter
import numpy as np
with SummaryWriter() as writer:
    writer.add_embedding(torch.stack([torch.mean(torch.squeeze(features[6]), dim=0)]).cpu(), metadata=["0"])

In [49]:
t = torch.stack([torch.mean(torch.squeeze(features[6]), dim=0)])
t.shape

torch.Size([1, 768])

In [52]:
import pandas as pd
df = pd.read_csv("bird_songs_metadata.csv")
df.head()

id       genus   species subspecies           name  \
0  557838  Thryomanes  bewickii        NaN  Bewick's Wren   
1  557838  Thryomanes  bewickii        NaN  Bewick's Wren   
2  557838  Thryomanes  bewickii        NaN  Bewick's Wren   
3  557838  Thryomanes  bewickii        NaN  Bewick's Wren   
4  557838  Thryomanes  bewickii        NaN  Bewick's Wren   

                recordist        country  \
0  Whitney Neufeld-Kaiser  United States   
1  Whitney Neufeld-Kaiser  United States   
2  Whitney Neufeld-Kaiser  United States   
3  Whitney Neufeld-Kaiser  United States   
4  Whitney Neufeld-Kaiser  United States   

                                  location  latitude  longitude altitude  \
0  Arlington, Snohomish County, Washington   48.0708  -122.1006      100   
1  Arlington, Snohomish County, Washington   48.0708  -122.1006      100   
2  Arlington, Snohomish County, Washington   48.0708  -122.1006      100   
3  Arlington, Snohomish County, Washington   48.0708  -122.1006      100   
4  Arlington, Snohomish County, Washington   48.0708  -122.1006      100   

                   sound_type                   source_url  \
0  adult, sex uncertain, song  //www.xeno-canto.org/557838   
1  adult, sex uncertain, song  //www.xeno-canto.org/557838   
2  adult, sex uncertain, song  //www.xeno-canto.org/557838   
3  adult, sex uncertain, song  //www.xeno-canto.org/557838   
4  adult, sex uncertain, song  //www.xeno-canto.org/557838   

                                        license   time        date  \
0  //creativecommons.org/licenses/by-nc-sa/4.0/  11:51  2020-03-14   
1  //creativecommons.org/licenses/by-nc-sa/4.0/  11:51  2020-03-14   
2  //creativecommons.org/licenses/by-nc-sa/4.0/  11:51  2020-03-14   
3  //creativecommons.org/licenses/by-nc-sa/4.0/  11:51  2020-03-14   
4  //creativecommons.org/licenses/by-nc-sa/4.0/  11:51  2020-03-14   

                                             remarks      filename  
0  Recorded with Voice Record Pro on iPhone7, nor...  557838-0.wav  
1  Recorded with Voice Record Pro on iPhone7, nor...  557838-1.wav  
2  Recorded with Voice Record Pro on iPhone7, nor...  557838-4.wav  
3  Recorded with Voice Record Pro on iPhone7, nor...  557838-5.wav  
4  Recorded with Voice Record Pro on iPhone7, nor...  557838-6.wav

In [62]:
from tqdm import tqdm
embs_by_layer = [[] for i in range(12)]
with torch.inference_mode():
    for fname in tqdm(df.filename):
        waveform, _ = torchaudio.load(f"wavfiles/{fname}")
        waveform = torchaudio.functional.resample(waveform, SAMPLE_RATE, bundle.sample_rate)
        features, _ = model.extract_features(waveform.to(device))
        for layer in range(12):
            embs_by_layer[layer].append(
                (torch.mean(torch.squeeze(features[layer]), dim=0)).cpu())


100%|██████████| 5422/5422 [03:07<00:00, 28.92it/s]


In [69]:
for layer in tqdm(range(12)):
    with SummaryWriter() as writer:
        writer.add_embedding(torch.stack(embs_by_layer[layer]), metadata=df.species)

100%|██████████| 12/12 [00:41<00:00,  3.45s/it]


In [76]:
import librosa
lbrs_embs = []
sampled = df.sample(500)
for fname in tqdm(sampled.filename):
    (waveform, sr) = librosa.load(f"wavfiles/{fname}")
    lbrs_embs.append(librosa.feature.chroma_cens(waveform, sr).flatten())

  5%|▍         | 23/500 [00:02<00:50,  9.49it/s]/home/jovvik/anaconda3/envs/ad7/lib/python3.9/site-packages/librosa/core/pitch.py:153: UserWarning: Trying to estimate tuning from empty frequency set.
  warnings.warn("Trying to estimate tuning from empty frequency set.")
100%|██████████| 500/500 [01:01<00:00,  8.15it/s]


In [77]:
with SummaryWriter() as writer:
    writer.add_embedding(np.array(lbrs_embs), metadata=sampled.species)

In [100]:
fst, sr1 = torchaudio.load("wavfiles/560427-5.wav")
snd, sr2 = torchaudio.load("wavfiles/565242-1.wav")

In [101]:
Audio(fst, sr1)

In [102]:
Audio(snd, sr2)